In [12]:
import csv
import os
from pathlib import Path
import glob
import pandas as pd
import datetime
from zipfile import ZipFile

### Extract data

In [19]:
!kaggle datasets download -d sudalairajkumar/cryptocurrencypricehistory

 59%|██████████████████████▎               | 1.00M/1.70M [00:00<00:00, 9.03MB/s]
100%|██████████████████████████████████████| 1.70M/1.70M [00:00<00:00, 10.4MB/s]


In [20]:
#extract the zip folder 
# Create a ZipFile Object and load zip in it
kaggle_download_datapath = os.getenv('kaggle_download_datapath') 
with ZipFile(kaggle_download_datapath+'cryptocurrencypricehistory.zip', 'r') as zipObj:
   # Extract all the contents of zip file in current directory
   zipObj.extractall('cryptocurrencypricehistory')

In [21]:
#combine all files of different crypto markets into one 
kaggle_dateset_path = Path(kaggle_download_datapath+'/cryptocurrencypricehistory')
filepaths = [f for f in kaggle_dateset_path.glob("*.csv") ]
df = pd.concat(map(pd.read_csv, filepaths))

In [22]:
df

SNo             Name Symbol                 Date          High  \
0      1              NEM    XEM  2015-04-02 23:59:59      0.000323   
1      2              NEM    XEM  2015-04-03 23:59:59      0.000330   
2      3              NEM    XEM  2015-04-04 23:59:59      0.000318   
3      4              NEM    XEM  2015-04-05 23:59:59      0.000283   
4      5              NEM    XEM  2015-04-06 23:59:59      0.000299   
..   ...              ...    ...                  ...           ...   
883  884  Wrapped Bitcoin   WBTC  2021-07-02 23:59:59  33841.008754   
884  885  Wrapped Bitcoin   WBTC  2021-07-03 23:59:59  34871.130346   
885  886  Wrapped Bitcoin   WBTC  2021-07-04 23:59:59  35914.361323   
886  887  Wrapped Bitcoin   WBTC  2021-07-05 23:59:59  35294.411111   
887  888  Wrapped Bitcoin   WBTC  2021-07-06 23:59:59  35004.772491   

              Low          Open         Close        Volume     Marketcap  
0        0.000227      0.000242      0.000314  2.854940e+04  2.823534e+06  
1        0.000291      0.000309      0.000310  2.067790e+04  2.792457e+06  
2        0.000251      0.000310      0.000277  2.355020e+04  2.488770e+06  
3        0.000218      0.000272      0.000232  2.680020e+04  2.087388e+06  
4        0.000229      0.000232      0.000289  2.251150e+04  2.598354e+06  
..            ...           ...           ...           ...           ...  
883  32761.826975  33529.259522  33824.263339  1.609147e+08  6.625345e+09  
884  33381.245301  33806.037094  34676.985915  1.659959e+08  6.792373e+09  
885  34382.512697  34672.651028  35289.762931  1.583060e+08  6.912401e+09  
886  33288.379267  35294.411111  33806.661764  1.711673e+08  6.621898e+09  
887  33700.560335  33772.552729  34189.372826  2.035448e+08  6.713947e+09  

[37082 rows x 10 columns]

In [23]:
df.Symbol.unique()

array(['XEM', 'EOS', 'XMR', 'DOT', 'USDC', 'UNI', 'BNB', 'MIOTA', 'AAVE',
       'SOL', 'BTC', 'ADA', 'USDT', 'ATOM', 'LINK', 'LTC', 'XRP', 'ETH',
       'TRX', 'XLM', 'CRO', 'DOGE', 'WBTC'], dtype=object)

In [24]:
##export data frame as csv
combined_csv_datapath = kaggle_download_datapath+'/crypto_combined_dataset.csv'
df.to_csv(combined_csv_datapath)

In [25]:
##count number of rows wih missing data
df.isnull().values.ravel().sum()

0

In [26]:
##read combined_csv file 
crpyto_data_file = open(combined_csv_datapath)
csv_reader = csv.reader(crpyto_data_file)
print(csv_reader)

In [27]:
df.dtypes

SNo            int64
Name          object
Symbol        object
Date          object
High         float64
Low          float64
Open         float64
Close        float64
Volume       float64
Marketcap    float64
dtype: object

### Transform Data

In [28]:
##we need to convert datatype of Date from object to datetime64
crypto_data = []

next(csv_reader,None) #to skip row 1 i.e. header row

for row in csv_reader:
    row[4] = datetime.datetime.strptime(row[4], '%Y-%m-%d %H:%M:%S')
    crypto_data.append(row)
    

print(len(crypto_data))
print(crypto_data[:2])    
    
    

37082
[['0', '1', 'NEM', 'XEM', datetime.datetime(2015, 4, 2, 23, 59, 59), '0.0003230780130252', '0.0002272779966006', '0.0002421469980617', '0.000313725991873', '28549.400390625', '2823533.99969'], ['1', '2', 'NEM', 'XEM', datetime.datetime(2015, 4, 3, 23, 59, 59), '0.0003296759969089', '0.0002907729940488', '0.0003087499935645', '0.0003102729970123', '20677.900390625', '2792456.99969']]


### Loading the data into MySQL

In [17]:
#!pip3  install mysql-connector-python

     |████████████████████████████████| 302 kB 1.5 MB/s            
     |████████████████████████████████| 1.0 MB 274 kB/s            


In [39]:
from mysql import connector
from mysql.connector import (connection)
from mysql.connector import errorcode

In [40]:
user = os.getenv('mysql_usrname')
passsword = os.getenv('mysql_password')

In [41]:
config = {
  'user': user,
  'password': passsword,
  'host': '127.0.0.1',
  'raise_on_warnings': True
}

try:
    conn = connector.connect(**config)
except connector.Error as err:
    if err.errno == errorcode.ER_ACCESS_DENIED_ERROR:
        print("Something is wrong with your user name or password")
    elif err.errno == errorcode.ER_BAD_DB_ERROR:
        print("Database does not exist")
    else:
        print(err)     


In [42]:
#creating a cursor object using cursor() method
cursor = conn.cursor()

### create database

In [43]:
#Doping database MYDATABASE if already exists.
try:
    cursor.execute("DROP database IF EXISTS cryptomarkets")
except Exception as e:
    print(str(e))

#Preparing query to create a database
sql = "CREATE database cryptomarkets";

#Creating a database
try:
    cursor.execute(sql)
except Exception as e:
    print(str(e))

#Retrieving the list of databases
print("List of databases: ")
sql_query = "SHOW DATABASES"

try:
    cursor.execute(sql_query)
except Exception as e:
    print(str(e))
print(cursor.fetchall())

#use database cryptomarkets
sql_query = "USE cryptomarkets"

try:
    cursor.execute(sql_query)
except Exception as e:
    print(str(e))

List of databases: 
[('Admission',), ('Airline',), ('Bucketlist',), ('collegeAdmission',), ('crypto',), ('cryptomarkets',), ('drinks',), ('gregs_list',), ('headfirst',), ('information_schema',), ('mysql',), ('performance_schema',), ('sys',), ('twitterdb',)]


### Create crypto table

In [44]:
# Drop a table name Crypto id it exists already
try:
    cursor.execute('DROP TABLE IF EXISTS Crypto ')
except Exception as e:
    print(str(e))
    
# Create a new Table named as Crypto
try:
    cursor.execute('''
         CREATE TABLE Crypto
         (ID         INTEGER PRIMARY KEY NOT NULL AUTO_INCREMENT,
         Name        TEXT    NOT NULL,
         Date        datetime,
         High        Float DEFAULT 0,
         Low        Float DEFAULT 0,
         Open         Float DEFAULT 0,
         Close       Float DEFAULT 0);''')
    print ("Table created successfully");
except Exception as e:
    print(str(e))
    print('Table Creation Failed!!!!!')
finally:
    conn.close() # this closes the database connection

1051: Unknown table 'cryptomarkets.crypto'
Table created successfully


In [45]:
# Since our crypto data contains more information than required so we need eliminate some of it.
print(crypto_data[0])

['0', '1', 'NEM', 'XEM', datetime.datetime(2015, 4, 2, 23, 59, 59), '0.0003230780130252', '0.0002272779966006', '0.0002421469980617', '0.000313725991873', '28549.400390625', '2823533.99969']


In [46]:
crypto_sql_data = []
crypto_sql_data = [(row[2], row[4], row[5], row[6], row[7], row[8]) for row in crypto_data]
crypto_sql_data[:2]

[('NEM',
  datetime.datetime(2015, 4, 2, 23, 59, 59),
  '0.0003230780130252',
  '0.0002272779966006',
  '0.0002421469980617',
  '0.000313725991873'),
 ('NEM',
  datetime.datetime(2015, 4, 3, 23, 59, 59),
  '0.0003296759969089',
  '0.0002907729940488',
  '0.0003087499935645',
  '0.0003102729970123')]

In [48]:
#make new connection to Insert crypto data in mysql
config = {
  'user': user,
  'password': passsword,
  'host': '127.0.0.1',
  'database':'cryptomarkets',
  'raise_on_warnings': True
}

try:
    conn = connector.connect(**config)
except connector.Error as err:
    if err.errno == errorcode.ER_ACCESS_DENIED_ERROR:
        print("Something is wrong with your user name or password")
    elif err.errno == errorcode.ER_BAD_DB_ERROR:
        print("Database does not exist")
    else:
        print(err) 

In [49]:
#creating a cursor object using cursor() method
cursor = conn.cursor()

In [50]:
try:
    cursor.executemany("INSERT INTO Crypto(Name, Date, Open, High, Low, Close) VALUES (%s,%s,%s,%s,%s,%s)", crypto_sql_data)
    conn.commit()
    print('Data Inserted Successfully')
except Exception as e:
    print(str(e))
    print('Data Insertion Failed')
finally:
    conn.close()

Data Inserted Successfully


### Reading data to verify

In [51]:
#create connection to mysql cryptomarkets db
#make new connection to Insert crypto data in mysql
config = {
  'user': user,
  'password': passsword,
  'host': '127.0.0.1',
  'database':'cryptomarkets',
  'raise_on_warnings': True
}

try:
    conn = connector.connect(**config)
except connector.Error as err:
    if err.errno == errorcode.ER_ACCESS_DENIED_ERROR:
        print("Something is wrong with your user name or password")
    elif err.errno == errorcode.ER_BAD_DB_ERROR:
        print("Database does not exist")
    else:
        
        print(err) 

In [52]:
cursor = conn.cursor(buffered=True)
cursor.reset()
sql_query = "SELECT * FROM Crypto"
cursor.execute(sql_query)
rows = cursor.fetchall()
header = [row[0] for row in cursor.description]

conn.close()

In [53]:
for row in rows:
    print(row)

(1, 'NEM', datetime.datetime(2015, 4, 2, 23, 59, 59), 0.000227278, 0.000242147, 0.000323078, 0.000313726)
(2, 'NEM', datetime.datetime(2015, 4, 3, 23, 59, 59), 0.000290773, 0.00030875, 0.000329676, 0.000310273)
(3, 'NEM', datetime.datetime(2015, 4, 4, 23, 59, 59), 0.000250514, 0.000310235, 0.000318236, 0.00027653)
(4, 'NEM', datetime.datetime(2015, 4, 5, 23, 59, 59), 0.000218265, 0.000271524, 0.000282632, 0.000231932)
(5, 'NEM', datetime.datetime(2015, 4, 6, 23, 59, 59), 0.000229368, 0.000232042, 0.000298683, 0.000288706)
(6, 'NEM', datetime.datetime(2015, 4, 7, 23, 59, 59), 0.000233713, 0.00028846, 0.00028846, 0.000240521)
(7, 'NEM', datetime.datetime(2015, 4, 8, 23, 59, 59), 0.000223208, 0.000245472, 0.000258572, 0.00022787)
(8, 'NEM', datetime.datetime(2015, 4, 9, 23, 59, 59), 0.000212816, 0.000227618, 0.00023903, 0.000224182)
(9, 'NEM', datetime.datetime(2015, 4, 10, 23, 59, 59), 0.000167379, 0.000224198, 0.000226941, 0.000174693)
(10, 'NEM', datetime.datetime(2015, 4, 11, 23, 59, 

(1818, 'NEM', datetime.datetime(2020, 3, 23, 23, 59, 59), 0.0358842, 0.0365115, 0.0399593, 0.0398579)
(1819, 'NEM', datetime.datetime(2020, 3, 24, 23, 59, 59), 0.0368417, 0.0398052, 0.0456935, 0.0394966)
(1820, 'NEM', datetime.datetime(2020, 3, 25, 23, 59, 59), 0.0380651, 0.039484, 0.0397112, 0.0384423)
(1821, 'NEM', datetime.datetime(2020, 3, 26, 23, 59, 59), 0.0374635, 0.0382827, 0.0396069, 0.0395718)
(1822, 'NEM', datetime.datetime(2020, 3, 27, 23, 59, 59), 0.038165, 0.0395879, 0.0402274, 0.0381993)
(1823, 'NEM', datetime.datetime(2020, 3, 28, 23, 59, 59), 0.0359596, 0.0381626, 0.0384157, 0.0369497)
(1824, 'NEM', datetime.datetime(2020, 3, 29, 23, 59, 59), 0.0355182, 0.0369428, 0.042754, 0.035912)
(1825, 'NEM', datetime.datetime(2020, 3, 30, 23, 59, 59), 0.0357622, 0.0358982, 0.0380372, 0.0369171)
(1826, 'NEM', datetime.datetime(2020, 3, 31, 23, 59, 59), 0.0354682, 0.0370694, 0.038078, 0.0365152)
(1827, 'NEM', datetime.datetime(2020, 4, 1, 23, 59, 59), 0.0347994, 0.0365152, 0.037128

(3317, 'EOS', datetime.datetime(2020, 4, 25, 23, 59, 59), 2.69291, 2.71919, 2.76845, 2.7163)
(3318, 'EOS', datetime.datetime(2020, 4, 26, 23, 59, 59), 2.70498, 2.71615, 2.77302, 2.73512)
(3319, 'EOS', datetime.datetime(2020, 4, 27, 23, 59, 59), 2.71697, 2.73572, 2.81551, 2.74626)
(3320, 'EOS', datetime.datetime(2020, 4, 28, 23, 59, 59), 2.71817, 2.74595, 2.78875, 2.78332)
(3321, 'EOS', datetime.datetime(2020, 4, 29, 23, 59, 59), 2.77002, 2.78649, 3.04922, 3.01786)
(3322, 'EOS', datetime.datetime(2020, 4, 30, 23, 59, 59), 2.80536, 3.01763, 3.10378, 2.83337)
(3323, 'EOS', datetime.datetime(2020, 5, 1, 23, 59, 59), 2.8321, 2.83425, 2.93516, 2.88669)
(3324, 'EOS', datetime.datetime(2020, 5, 2, 23, 59, 59), 2.86813, 2.88653, 2.94608, 2.94608)
(3325, 'EOS', datetime.datetime(2020, 5, 3, 23, 59, 59), 2.80781, 2.94598, 3.00038, 2.84232)
(3326, 'EOS', datetime.datetime(2020, 5, 4, 23, 59, 59), 2.67929, 2.84198, 2.85137, 2.78143)
(3327, 'EOS', datetime.datetime(2020, 5, 5, 23, 59, 59), 2.74255, 

(5299, 'Monero', datetime.datetime(2018, 8, 14, 23, 59, 59), 79.2381, 88.0255, 88.0255, 84.1787)
(5300, 'Monero', datetime.datetime(2018, 8, 15, 23, 59, 59), 84.5871, 84.5871, 94.0233, 89.5485)
(5301, 'Monero', datetime.datetime(2018, 8, 16, 23, 59, 59), 88.952, 89.3508, 92.6471, 91.0785)
(5302, 'Monero', datetime.datetime(2018, 8, 17, 23, 59, 59), 90.829, 91.006, 101.163, 99.2022)
(5303, 'Monero', datetime.datetime(2018, 8, 18, 23, 59, 59), 95.1047, 99.4128, 104.902, 98.1654)
(5304, 'Monero', datetime.datetime(2018, 8, 19, 23, 59, 59), 94.9965, 98.2142, 98.8563, 98.4241)
(5305, 'Monero', datetime.datetime(2018, 8, 20, 23, 59, 59), 93.3748, 98.3955, 102.053, 93.3748)
(5306, 'Monero', datetime.datetime(2018, 8, 21, 23, 59, 59), 92.2503, 93.2037, 96.5119, 94.9158)
(5307, 'Monero', datetime.datetime(2018, 8, 22, 23, 59, 59), 88.3314, 94.9507, 98.5623, 90.0806)
(5308, 'Monero', datetime.datetime(2018, 8, 23, 23, 59, 59), 88.8997, 89.8706, 91.38, 90.0629)
(5309, 'Monero', datetime.datetime(

(6316, 'Monero', datetime.datetime(2021, 5, 27, 23, 59, 59), 243.892, 268.815, 269.394, 250.67)
(6317, 'Monero', datetime.datetime(2021, 5, 28, 23, 59, 59), 219.598, 251.823, 266.45, 262.821)
(6318, 'Monero', datetime.datetime(2021, 5, 29, 23, 59, 59), 229.772, 262.518, 296.696, 242.684)
(6319, 'Monero', datetime.datetime(2021, 5, 30, 23, 59, 59), 226.916, 242.998, 267.651, 262.334)
(6320, 'Monero', datetime.datetime(2021, 5, 31, 23, 59, 59), 243.029, 261.929, 275.836, 272.919)
(6321, 'Monero', datetime.datetime(2021, 6, 1, 23, 59, 59), 253.315, 272.445, 275.657, 265.775)
(6322, 'Monero', datetime.datetime(2021, 6, 2, 23, 59, 59), 262.829, 266.43, 294.982, 294.092)
(6323, 'Monero', datetime.datetime(2021, 6, 3, 23, 59, 59), 286.448, 294.706, 315.664, 308.189)
(6324, 'Monero', datetime.datetime(2021, 6, 4, 23, 59, 59), 268.867, 309.497, 310.882, 287.464)
(6325, 'Monero', datetime.datetime(2021, 6, 5, 23, 59, 59), 257.824, 287.833, 295.112, 264.308)
(6326, 'Monero', datetime.datetime(202

...

(31064, 'Stellar', datetime.datetime(2017, 8, 1, 23, 59, 59), 0.0158665, 0.016102, 0.0179554, 0.0179332)
(31065, 'Stellar', datetime.datetime(2017, 8, 2, 23, 59, 59), 0.0175266, 0.0179059, 0.0191882, 0.0184128)
(31066, 'Stellar', datetime.datetime(2017, 8, 3, 23, 59, 59), 0.0182071, 0.0183129, 0.0189807, 0.0188598)
(31067, 'Stellar', datetime.datetime(2017, 8, 4, 23, 59, 59), 0.018597, 0.0188463, 0.0224111, 0.022241)
(31068, 'Stellar', datetime.datetime(2017, 8, 5, 23, 59, 59), 0.0210513, 0.0227996, 0.0265378, 0.0239843)
(31069, 'Stellar', datetime.datetime(2017, 8, 6, 23, 59, 59), 0.0226179, 0.0238352, 0.0247226, 0.0227015)
(31070, 'Stellar', datetime.datetime(2017, 8, 7, 23, 59, 59), 0.0212221, 0.0226974, 0.0230503, 0.0221954)
(31071, 'Stellar', datetime.datetime(2017, 8, 8, 23, 59, 59), 0.0217034, 0.0222997, 0.0237371, 0.0237371)
(31072, 'Stellar', datetime.datetime(2017, 8, 9, 23, 59, 59), 0.0216009, 0.0238125, 0.0246131, 0.0229962)
(31073, 'Stellar', datetime.datetime(2017, 8, 10,

(32308, 'Stellar', datetime.datetime(2020, 12, 27, 23, 59, 59), 0.135361, 0.147044, 0.15493, 0.144973)
(32309, 'Stellar', datetime.datetime(2020, 12, 28, 23, 59, 59), 0.142134, 0.145099, 0.154212, 0.144375)
(32310, 'Stellar', datetime.datetime(2020, 12, 29, 23, 59, 59), 0.129052, 0.144359, 0.148768, 0.138815)
(32311, 'Stellar', datetime.datetime(2020, 12, 30, 23, 59, 59), 0.129891, 0.13876, 0.139266, 0.131913)
(32312, 'Stellar', datetime.datetime(2020, 12, 31, 23, 59, 59), 0.124408, 0.131989, 0.13216, 0.12837)
(32313, 'Stellar', datetime.datetime(2021, 1, 1, 23, 59, 59), 0.127367, 0.128321, 0.139801, 0.132408)
(32314, 'Stellar', datetime.datetime(2021, 1, 2, 23, 59, 59), 0.127561, 0.132471, 0.134618, 0.12782)
(32315, 'Stellar', datetime.datetime(2021, 1, 3, 23, 59, 59), 0.124531, 0.127847, 0.138974, 0.136423)
(32316, 'Stellar', datetime.datetime(2021, 1, 4, 23, 59, 59), 0.130889, 0.136644, 0.165951, 0.16518)
(32317, 'Stellar', datetime.datetime(2021, 1, 5, 23, 59, 59), 0.151998, 0.1650

(33844, 'Dogecoin', datetime.datetime(2015, 1, 29, 23, 59, 59), 0.000139418, 0.000145731, 0.000148191, 0.000146714)
(33845, 'Dogecoin', datetime.datetime(2015, 1, 30, 23, 59, 59), 0.000141947, 0.00014647, 0.00015089, 0.000142444)
(33846, 'Dogecoin', datetime.datetime(2015, 1, 31, 23, 59, 59), 0.000138077, 0.000142563, 0.000146474, 0.000139116)
(33847, 'Dogecoin', datetime.datetime(2015, 2, 1, 23, 59, 59), 0.000135795, 0.000138362, 0.000147294, 0.000143878)
(33848, 'Dogecoin', datetime.datetime(2015, 2, 2, 23, 59, 59), 0.000141714, 0.000143717, 0.000151552, 0.000151172)
(33849, 'Dogecoin', datetime.datetime(2015, 2, 3, 23, 59, 59), 0.000144384, 0.000150425, 0.00015564, 0.000147155)
(33850, 'Dogecoin', datetime.datetime(2015, 2, 4, 23, 59, 59), 0.000143224, 0.000147956, 0.000147956, 0.000146655)
(33851, 'Dogecoin', datetime.datetime(2015, 2, 5, 23, 59, 59), 0.00014029, 0.000147122, 0.000151888, 0.000142116)
(33852, 'Dogecoin', datetime.datetime(2015, 2, 6, 23, 59, 59), 0.00014008, 0.0001

(35421, 'Dogecoin', datetime.datetime(2019, 5, 25, 23, 59, 59), 0.00295786, 0.00299577, 0.0030106, 0.00299073)
(35422, 'Dogecoin', datetime.datetime(2019, 5, 26, 23, 59, 59), 0.0029346, 0.00298678, 0.00311504, 0.00309249)
(35423, 'Dogecoin', datetime.datetime(2019, 5, 27, 23, 59, 59), 0.00308643, 0.00309873, 0.00320706, 0.00314094)
(35424, 'Dogecoin', datetime.datetime(2019, 5, 28, 23, 59, 59), 0.00307141, 0.00314186, 0.00316822, 0.00314824)
(35425, 'Dogecoin', datetime.datetime(2019, 5, 29, 23, 59, 59), 0.00308294, 0.00314917, 0.00315055, 0.00312703)
(35426, 'Dogecoin', datetime.datetime(2019, 5, 30, 23, 59, 59), 0.00310967, 0.00312459, 0.00359959, 0.00325831)
(35427, 'Dogecoin', datetime.datetime(2019, 5, 31, 23, 59, 59), 0.00317169, 0.00325628, 0.00344324, 0.00344112)
(35428, 'Dogecoin', datetime.datetime(2019, 6, 1, 23, 59, 59), 0.00336012, 0.00344324, 0.00351988, 0.0034189)
(35429, 'Dogecoin', datetime.datetime(2019, 6, 2, 23, 59, 59), 0.00334232, 0.00342572, 0.0034478, 0.00339762

(36697, 'Wrapped Bitcoin', datetime.datetime(2020, 6, 16, 23, 59, 59), 9265.05, 9330.99, 9600.35, 9510.59)
(36698, 'Wrapped Bitcoin', datetime.datetime(2020, 6, 17, 23, 59, 59), 9338.9, 9515.66, 9613.86, 9436.56)
(36699, 'Wrapped Bitcoin', datetime.datetime(2020, 6, 18, 23, 59, 59), 9362.77, 9433.8, 9472.92, 9435.62)
(36700, 'Wrapped Bitcoin', datetime.datetime(2020, 6, 19, 23, 59, 59), 9214.99, 9431.0, 9469.51, 9236.41)
(36701, 'Wrapped Bitcoin', datetime.datetime(2020, 6, 20, 23, 59, 59), 9222.8, 9230.98, 9448.62, 9359.25)
(36702, 'Wrapped Bitcoin', datetime.datetime(2020, 6, 21, 23, 59, 59), 9285.95, 9361.84, 9542.1, 9411.46)
(36703, 'Wrapped Bitcoin', datetime.datetime(2020, 6, 22, 23, 59, 59), 9348.42, 9413.08, 10184.4, 9911.51)
(36704, 'Wrapped Bitcoin', datetime.datetime(2020, 6, 23, 23, 59, 59), 9693.72, 9913.33, 9947.23, 9729.22)
(36705, 'Wrapped Bitcoin', datetime.datetime(2020, 6, 24, 23, 59, 59), 9274.34, 9731.43, 9822.54, 9345.92)
(36706, 'Wrapped Bitcoin', datetime.dateti

In [ ]:
##export data from database to csv

In [54]:
 # Create csv file
f = open('crypto_final.csv', 'w')

# Write header
f.write(','.join(header) + '\n')

for row in rows:
    f.write(','.join(str(r) for r in row) + '\n')

f.close()
print(str(len(rows)) + ' rows written successfully to ' + f.name)

37082 rows written successfully to crypto_final.csv
